# Sonification of Kauai Topographical Point Cloud Data

## Data Source

* http://opentopo.sdsc.edu/datasets -- Hawaii Kauai Survey (Point Cloud Data)

## Preparation

See `01_export_frequencies.hiplc` (Houdini 16 Project File). General Idea:

1. Load LAS data into Houdini
2. Sample moving average of slices through point cloud data
3. Save each slice into a JSON file (array of 3-element arrays (points), only Y value is used)

![Houdini Screenshot](01_screenshot.png)


In [4]:
import io
import json
import os
import numpy as np
import wave

from IPython.display import Audio, HTML, display
from plotly.offline import init_notebook_mode, iplot
from plotly.graph_objs import Scattergl, Layout, Figure, Heatmap

init_notebook_mode(connected=True)  # Don't need a plot.ly account

SAMPLE_RATE = 44100


def overlap(a, b, n, func='linear'):
  """
  Overlap the arrays *a* and *b* by *n* elements and mix the overlapping
  elements by the linear weighting function *func* ([0, 1] -> [0, 1]).
  This is used to overlap time-domain signals to generate a smooth wave
  form (similar to overlap-add method).
  """

  if func == 'linear':
    def func(x): return x
  elif func == 'smoothcos':
    def func(x): return 1.0 - np.cos(x * np.pi) * 0.5 + 0.5
  elif func == 'square':
    def func(x): return x * x
  elif not callable(func):
    raise ValueError('invalid func: {!r}'.format(func))

  if n > a.shape[0]: n = a.shape[0]
  if n > b.shape[0]: n = b.shape[0]
  weights = func(np.linspace(0, 1, n))
  return np.concatenate([a[:-n], a[-n:] * (1 - weights) + b[:n] * weights, b[n:]])


def aggregate(val, values, func):
  """
  Simple aggregation function that takes an initial value *val* and calls
  *func* for every item in *values* with *val* as the first argument and
  the item as the second. The result of every call to *func* will be
  assigned to *val* and passed to the next call.

  Used to apply the #overlap() function to the time-domain signal buckets.
  """

  for x in values:
    val = func(val, x)
  return val


def normalize(array):
  """
  Maps the values in *array* from their current [min, max] to [-1, 1] range.
  """

  min_ = np.min(array)
  return (array - min_) / (np.max(array) - min_) * 2.0 - 1.0


def to_wav(waveform, fp=None, rate=SAMPLE_RATE):
  """
  Convert a waveform to a WAV audio file.
  """
  
  if waveform.dtype in (np.float32, np.float64):
    # TODO: Round to nearest integer (instead of floor).
    waveform = (waveform * (2**15-1)).astype(np.int16)
  assert waveform.dtype == np.int16

  if fp is None:
    fp = io.BytesIO()
  writer = wave.open(fp, 'w')
  writer.setnchannels(1)
  writer.setframerate(SAMPLE_RATE)
  writer.setsampwidth(2)
  writer.writeframes(waveform.tostring())
  return fp


def load_frequencies():
  """
  Loads the frequency buckets from the JSON files that have been exported
  from Houdini into a 2-d numpy array.
  """

  result = []
  dirname = os.path.join(os.getcwd(), '01_out')
  for fname in sorted(os.listdir(dirname)):
    with open(os.path.join(dirname, fname)) as fp:
      data = json.load(fp)
    data = [d[1] for d in data]
    result.append(data)
  
  return normalize(np.array(result))
  result = np.array(result)
  result -= np.average(result)
  min, max = np.min(result), np.max(result)
  return (result - min) / (max - min)

## Plot Input Data

*Compare the spectrogram with the image of the point cloud in Houdini above.*

In [5]:
frequencies = load_frequencies()

iplot(Figure(
  data = [ 
    Heatmap(
      x = np.arange(frequencies.shape[0]),
      y = np.arange(frequencies.shape[1]),
      z = frequencies.T
    )
  ],
  layout = Layout(
    title = 'Heatmap aka. Spectrogram',
    yaxis = {'title': 'Frequency'},
    xaxis = {'title': 'Time'}
  )
))

iplot(Figure(
  data = [
    Scattergl(
      x = np.arange(y.shape[0]),
      y = y - i*2 - 1
    )
    for i, y in enumerate(frequencies[::10])
  ],
  layout = Layout(
    title = 'Frequency Linegraph (every 10th frame)',
    yaxis = {'autotick': False, 'ticks': '', 'showticklabels': False, 'showgrid': False}
  )
))


## Convert frequencies to audio

### No time-domain overlap

In [6]:
FFT_LENGTH = 2048
PLOT_WIDTH = 20000

blocks = np.array([np.fft.irfft(x, FFT_LENGTH).real for x in frequencies])

signal = normalize(blocks.flatten())
display(Audio(to_wav(signal).getvalue()))

iplot([Scattergl(
    x = np.arange(PLOT_WIDTH),
    y = signal[:PLOT_WIDTH]
)])

## With time-domain overlap (smoother waveform)

In [7]:
OVERLAP = 128
FFT_SAMPLE = FFT_LENGTH - OVERLAP

def agg_signal(buckets):
  func = lambda agg, arr: overlap(agg, arr, OVERLAP)
  return aggregate(np.zeros(FFT_LENGTH), buckets, func)[FFT_SAMPLE:]

signal = agg_signal(blocks)
display(Audio(to_wav(normalize(signal)).getvalue()))

iplot([Scattergl(
    x = np.arange(PLOT_WIDTH),
    y = signal[:PLOT_WIDTH]
)])